In [1]:
import sys
if ".." not in sys.path:
    sys.path.insert(0, "..")

In [2]:
import os
from datetime import date, timedelta
import pandas as pd
import numpy as np
from information.terms_info import tags

pd.set_option('display.max_columns', None)
print(f'{tags}')

['flu', 'cough', 'fever', 'headache', 'lagnat', 'rashes', 'sipon', 'ubo', 'ecq', 'face-shield', 'Frontliners', 'masks', 'Quarantine', 'social-distancing', 'work-from-home']


In [3]:
"""
 Declare data scope
"""
# start_date = date.fromisoformat('2020-01-01')
start_date = date.fromisoformat('2020-03-16')
end_date   = date.fromisoformat('2021-02-15')

end_dates = []
current_date = start_date
while (current_date <= end_date):
    end_dates.append(str(current_date).replace('-', ' '))
    current_date += timedelta(days=1)
print(f"{len(end_dates)=}")

len(end_dates)=337


In [4]:
# ... existing code ...
for tag in tags:
    normalize_tag = tag.replace('/', '.')
    msv_df_csv_path = os.path.abspath(f'./../msvs/processed/{normalize_tag}.csv')
    msv_df_pkl_path = os.path.abspath(f'./../msvs/processed/{normalize_tag}.pkl')

    msv_df = None

    for current_date in end_dates:
        current_rsv_path = os.path.join(r"C:\Users\Cheska\Documents\GitHub\-Thesis-Infodemiology-GT\covid-19-google-trends-network\scripts\msvs\data", normalize_tag, f"{current_date}.csv")
        rsv_df = pd.read_csv(current_rsv_path, parse_dates=['date'])
        rsv_df.drop(columns=['isPartial'], inplace=True)
        rsv_df.columns = ['date', 'index']
        # Replace 0s with 0.01 in the 'index' column
        rsv_df['index'] = rsv_df['index'].replace(0, 0.01)

        if msv_df is None:
            msv_df = rsv_df.copy()
        else:
            # Join data into one
            merged_df = msv_df.merge(rsv_df, on='date', how='outer')

            # Calculate correction factors
            merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
            merged_df['correction_factor'] = merged_df['correction_factor'].fillna(1)
            merged_df['correction_factor'] = merged_df['correction_factor'].replace([np.inf, -np.inf], np.nan)
            aggregated_correction_factor = merged_df['correction_factor'].mean()

            # Rescale the new RSV
            merged_df['index_y'] = merged_df['index_y'] * aggregated_correction_factor

            # Fill new data into previous RSV/MSV
            merged_df['index_x'] = merged_df['index_x'].fillna(merged_df['index_y'])
            print(merged_df.tail())
            
            msv_df = merged_df[['date', 'index_x']].copy()
            msv_df.columns = ['date', 'index']

        print(rsv_df.describe())
        
    msv_df.to_csv(msv_df_csv_path, index=False)
    msv_df.to_pickle(msv_df_pkl_path)

# ... rest of the code ...

                      date       index
count                   31   31.000000
mean   2020-03-31 00:00:00   25.612903
min    2020-03-16 00:00:00   12.000000
25%    2020-03-23 12:00:00   15.500000
50%    2020-03-31 00:00:00   21.000000
75%    2020-04-07 12:00:00   31.000000
max    2020-04-15 00:00:00  100.000000
std                    NaN   16.819983
         date    index_x    index_y  correction_factor
27 2020-04-12  12.000000  48.746135           2.083333
28 2020-04-13  15.000000  58.495362           2.000000
29 2020-04-14  13.000000  50.695980           2.000000
30 2020-04-15  13.000000  52.645826           2.076923
31 2020-04-16  37.047062  37.047062           1.000000
                      date       index
count                   31   31.000000
mean   2020-04-01 00:00:00   45.645161
min    2020-03-17 00:00:00   19.000000
25%    2020-03-24 12:00:00   30.500000
50%    2020-04-01 00:00:00   41.000000
75%    2020-04-08 12:00:00   56.000000
max    2020-04-16 00:00:00  100.000000
std    

: 

In [10]:
for tag in tags:
    normalize_tag = tag.replace('/', '.')
    #rsv_directory = os.path.abspath()
    msv_df_csv_path = os.path.abspath(f'./../msvs/processed/{normalize_tag}.csv')
    msv_df_pkl_path = os.path.abspath(f'./../msvs/processed/{normalize_tag}.pkl')

    msv_df = None

    for current_date in end_dates:
        current_rsv_path = os.path.join("C:\\Users\\Cheska Hung\\Desktop\\Thesis-GT Infodemiology\\-Thesis-Infodemiology-GT\\covid-19-google-trends-network\\scripts\\msvs\\data", normalize_tag, f"{current_date}.csv")
        rsv_df = pd.read_csv(current_rsv_path, parse_dates=['date'])
        rsv_df.drop(columns=['isPartial'], inplace=True)
        rsv_df.columns = ['date', 'index']

        if msv_df is None:
            msv_df = rsv_df.copy()
        else:
            # Join data into one
            merged_df = msv_df.merge(rsv_df, on='date', how='outer')

            # Calculate correction factors
            merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
            merged_df['correction_factor'] = merged_df['correction_factor'].fillna(1)
            merged_df['correction_factor'] = merged_df['correction_factor'].round(4)
            aggregated_correction_factor = merged_df['correction_factor'].mean()

            # Resclae the new RSV
            merged_df['index_y'] = merged_df['index_y'] * aggregated_correction_factor

            # Fill new data into previous RSV/MSV
            merged_df['index_x'] = merged_df['index_x'].fillna(merged_df['index_y'])
            print(merged_df.tail())
            
            msv_df = merged_df[['date', 'index_x']].copy()
            msv_df.columns = ['date', 'index']

        print(rsv_df.describe())
        
    msv_df.to_csv(msv_df_csv_path, index=False)
    msv_df.to_pickle(msv_df_pkl_path)

FileNotFoundError: [Errno 2] No such file or directory: 'C:\\Users\\Cheska Hung\\Desktop\\Thesis-GT Infodemiology\\-Thesis-Infodemiology-GT\\covid-19-google-trends-network\\scripts\\msvs\\data\\flu\\2020 03 16.csv'